In [1]:
# @hidden_cell
# The following code contains the credentials for a file in your IBM Cloud Object Storage.
# You might want to remove those credentials before you share your notebook.
credentials_2 = {
    'IAM_SERVICE_ID': 'iam-ServiceId-05670e26-425c-4505-8824-ef9ea437d9c0',
    'IBM_API_KEY_ID': 'MaNADuPAUY6W0HC-8FxqIqpgji1yUUm6WVPlm9ulZIOW',
    'ENDPOINT': 'https://s3-api.us-geo.objectstorage.service.networklayer.com',
    'IBM_AUTH_ENDPOINT': 'https://iam.ng.bluemix.net/oidc/token',
    'BUCKET': 'nystesting-donotdelete-pr-yczufeevob9sat',
    'FILE': 'ManhattanLatLong.csv'
}

bingMapsKey = "AvDnxBjHKE2Y9SU1HRUpB6-79B0Bk_ldW-LCvqWkLWedsqWrlBX0kvkvl4JurmDO"


In [2]:
# @hidden_cell
# The project token is an authorization token that is used to access project resources like data sources, connections, and used by platform APIs.
from project_lib import Project
project = Project(project_id='994f2a2f-d34c-428b-8963-154fd9fac775', project_access_token='p-a6c7ad6d54b86c48f27bb6924d28f925b70b5c08')
pc = project.project_context

## FourSquare

In [3]:
import requests # library to handle requests
import pandas as pd # library for data analsysis
# tranforming json file into a pandas dataframe library
from pandas.io.json import json_normalize

In [4]:
# @hidden_cell
# FourSquare API credentials
CLIENT_ID = 'UYWTHYG53L3ENHJ4O50HDEHZKE51X0NPSR3YCXC1I0JCDGRA' # your Foursquare ID
CLIENT_SECRET = 'OPBF0AHVEAL11QB0HZUIWHP2BAUWQLZY4U0ZF10USQQVF0PJ' # your Foursquare Secret
numFourSquareCalls = 0

In [7]:
# import necessary packages to work with spatial data in Python
import os
import math
import numpy as np
import geopandas as gpd
import matplotlib.pyplot as plt
import matplotlib.lines as mlines
from matplotlib.colors import ListedColormap
import json
from tabulate import tabulate
import time
#import earthpy as et 

In [190]:
###### Retrieve all categories and sub-categories from FourSquare
VERSION = '20180604'
LIMIT=50
url = 'https://api.foursquare.com/v2/venues/categories?client_id={}&client_secret={}&v={}'.format(CLIENT_ID, CLIENT_SECRET, VERSION)
results = requests.get(url).json()
numFourSquareCalls = numFourSquareCalls + 1

# assign relevant part of JSON to categories
categories = results['response']['categories']
#print(categories)

# tranform categories into a dataframe
dfCategories = json_normalize(categories)

# Each category in the DF contains sub-categories. We want all the
# categories and sub-categories flattened into one DF.
# Create an empty list. We'll keep appending categories and 
# sub-categories to that list, then we'll turn that list into a DF
allCategoriesList = []

nRowCount = 0
for row in dfCategories.itertuples():
#    print(row.name)
    # First, put the parent category into the list
    # Use the category name for both the parent and category names
    rowData = [row.name, row.name, row.id]
    parentCategoryName = row.name;
    allCategoriesList.append(rowData)

    # Make a dictionary of the sub-categories of this category
    subCats = row.categories
    nRowCount = nRowCount + 1

    # Iterate over the sub-categories, adding each one to the list
    # Include the parent category's name
    for subCatRow in subCats:
#        print(subCatRow)
#        print("")
        subCatID = subCatRow['id']
        subCatName = subCatRow['name']
#        print('  ' + subCatName)
        rowData = [subCatName, parentCategoryName, subCatID]
        allCategoriesList.append(rowData)
        nRowCount = nRowCount + 1

        # Make a dictionary of the sub-sub-categories of this category
        subSubCats = subCatRow['categories']
        for subSubCatRow in subSubCats:
            subSubCatID = subSubCatRow['id']
            subSubCatName = subSubCatRow['name']
#            print('    ' + subSubCatRow)
            rowData = [subSubCatName, subCatName, subSubCatID]
            allCategoriesList.append(rowData)

# Now make a DF of the flattened categories and sub-categories
dfAllCategories = pd.DataFrame(allCategoriesList)
dfAllCategories.columns = ['name', 'parentCategoryName', 'id']

# Set the index of the DF to the category/sub-category name, because we'll
# retrieve IDs by name
dfAllCategories = dfAllCategories.set_index(['name'])

print("There are " + str(dfAllCategories.shape[0]) + " categories and sub-categories in FourSquare")
# Show the data
#print(tabulate(dfAllCategories, headers=['Name', 'Parent', 'ID']))

There are 833 categories and sub-categories in FourSquare


### Read in CSV files

### A user of this notebook can define which categories they want to analyze and map. For each category, they should also define what color they want map markers to be for that category, and which icon to use.

In [234]:
# You can change and/or add categories to explore in categoriesToFind
#categoriesToFind = ['Movie Theater', 'Juice Bar']
categoriesToFind = ['Mexican Restaurant', 'Jazz Club']
#categoriesToFind = ['Food', 'Clothing Store']

for aCategory in categoriesToFind:
    print('{} category\'s ID is {}'.format(aCategory, dfAllCategories.loc[aCategory]['id']))
    
# For each category listed above, define the map marker color and icon to use
# Icons are available from these sites:
#   https://fontawesome.com/icons?d=gallery&m=free
#   https://getbootstrap.com/docs/3.3/components/
# The fields are category, color, icon_prefix, and icon_name
#                    {'category':categoriesToFind[1], 'color':'orange', 'icon_prefix':'glyphicon', 'icon_name':'glyphicon-cutlery'}
categoryMapSpecs = [{'category':categoriesToFind[0], 'color':'red', 'icon_prefix':'fa', 'icon_name':'fa-film'},
                    {'category':categoriesToFind[1], 'color':'black', 'icon_prefix':'fa', 'icon_name':'fa-music'}
                   ]
dfMapMarkers = pd.DataFrame.from_dict(categoryMapSpecs)
dfMapMarkers.set_index('category', inplace=True)
#print(dfMapMarkers.loc[categoriesToFind[0]].index)
print('Color is {}'.format(dfMapMarkers.loc[categoriesToFind[0]].color))

Mexican Restaurant category's ID is 4bf58dd8d48988d1c1941735
Jazz Club category's ID is 4bf58dd8d48988d1e7931735
Color is red


In [197]:
import io

# Read the file containing the overlapping rectangles for Manhattan
wrapper = io.TextIOWrapper(project.get_file("ManhattanLatLong.csv"), encoding='utf-8')
dfManhattanLatLon = pd.read_csv(wrapper)
dfManhattanLatLon.head()

SWLAT      SWLON      NELAT      NELON
0  40.702142 -74.020323  40.707819 -74.002770
1  40.708046 -74.020688  40.715301 -73.981388
2  40.715203 -74.020655  40.724255 -73.978491
3  40.724190 -74.014841  40.730639 -73.977660
4  40.730671 -74.014009  40.737598 -73.978604

In [198]:
# Read the file containing the overlapping rectangles for Manhattan
wrapper = io.TextIOWrapper(project.get_file("BrooklynLatLong.csv"), encoding='utf-8')
dfBrooklynLatLon = pd.read_csv(wrapper)
dfBrooklynLatLon.head()

SWLAT      SWLON      NELAT      NELON
0  40.586324 -74.049198  40.637928 -73.894187
1  40.636756 -74.048168  40.678819 -73.871871
2  40.679470 -74.033233  40.703939 -73.886806
3  40.700035 -74.016925  40.710000 -73.898994
4  40.720000 -74.016925  40.729571 -73.898994

In [194]:
### DEBUGGING
dfAllVenues = pd.DataFrame()
categoryName = categoriesToFind[0]
categoryID = dfAllCategories.loc[categoryName]['id']

swLat = 40.75
swLon = -74.009432
neLat = 40.75689
neLon = -73.953926

url = 'https://api.foursquare.com/v2/venues/search?intent=browse&client_id={}&client_secret={}&sw={},{}&ne={},{}&v={}&categoryId={}&limit={}'\
.format(CLIENT_ID, CLIENT_SECRET, swLat, swLon, neLat, neLon, VERSION, categoryID, LIMIT)
results = requests.get(url).json()
venues = results['response']['venues']
print(len(venues))


21


In [32]:
### DEBUGGING
dfAllVenues = pd.DataFrame()
categoryName = categoriesToFind[0]
categoryID = dfAllCategories.loc[categoryName]['id']

swLat = 40.75
swLon = -74.009432
neLat = 40.751
neLon = -73.953926

url = 'https://api.foursquare.com/v2/venues/search?intent=browse&client_id={}&client_secret={}&sw={},{}&ne={},{}&v={}&categoryId={}&limit={}'\
.format(CLIENT_ID, CLIENT_SECRET, swLat, swLon, neLat, neLon, VERSION, categoryID, LIMIT)
results = requests.get(url).json()
venues = results['response']['venues']
print(len(venues))

dfOneRect = json_normalize(venues)
dfOneRect['category'] = categoryName

dfAllVenues = pd.concat([dfAllVenues, dfOneRect], sort=False)

swLat = 40.755
neLat = 40.76
url = 'https://api.foursquare.com/v2/venues/search?intent=browse&client_id={}&client_secret={}&sw={},{}&ne={},{}&v={}&categoryId={}&limit={}'\
.format(CLIENT_ID, CLIENT_SECRET, swLat, swLon, neLat, neLon, VERSION, categoryID, LIMIT)
results = requests.get(url).json()
venues = results['response']['venues']

dfOneRect = json_normalize(venues)
dfOneRect['category'] = categoryName

dfAllVenues = pd.concat([dfAllVenues, dfOneRect], sort=False)
numVenuesInRect = dfOneRect.shape[0]
print(numVenuesInRect)



2
40


In [41]:
### DEBUGGING
allVenues.head()
dfAllVenues.groupby(['id']).name.agg('count').to_frame('id')

KeyError: 'id'

In [199]:
# Make an enpty dataframe that will contains all the venues found
# for all the categories of interest, in all the rectangles in Manhattan
dfAllVenues = pd.DataFrame()

# Merge the two Lat/Lon CSV-based DataFrames
dfTwoBoroughsLatLon = pd.concat([dfManhattanLatLon, dfBrooklynLatLon])

for aCategory in categoriesToFind:
    # Get the ID of the category
    categoryName = aCategory
    categoryID = dfAllCategories.loc[categoryName]['id']
    print('Retrieving ' + categoryName)
    
    numVenuesRetrieved = 0
    numRoundedVenuesRetrieved = 0

    # Iterate over the rectangles, retrieving a list of venues for the category
    for row in dfTwoBoroughsLatLon.itertuples():
        swLat = row.SWLAT
        swLon = row.SWLON
        neLat = row.NELAT
        neLon = row.NELON
        
        # Every degree of latitude is approximately 69 miles 
        # (a little more at the North and South poles, a little less in the middle,
        # but 69 is good enough for our needs).
        # Because FourSquare will only return 50 venues at a time,
        # we need to request small slices of latitude, because in certain
        # areas of NYC, there are a lot of juice bars (or movie theaters, or whatever).
        # So figure out how many slices we need to limit the vertical size of the 
        # slice to about 1/10th of a mile
        differenceInLatitude = (neLat-swLat)
        numLatSlices = math.ceil((differenceInLatitude*69) / 0.10)
        
        numLatSlices = 1
        #print('neLat {} swLat {} differenceInLatitude={} numLatSlices {}'.format(neLat, swLat, differenceInLatitude, numLatSlices))
        
        # Break the rectangle up into numLatSlices rectangles,  and create a list
        # with numLatSlices values for swLat, so that a smaller area gets retrieved from FourSquare.
        # This is necessary because some venue categories have more than the maximum
        # number of venues (50) FourSquare will return from one call.
        swLatList = np.linspace(swLat, neLat, numLatSlices, endpoint=True)
        numSWLats = len(swLatList)
        
        # We also need to slice the longitude, because requesting 1/10th of mile latitude by 2.5 miles longitude
        # still results in more than 50 venues sometimes.
        #differenceInLongitude = (neLon-swLon)
        #numLonSlices = 3
        numLonSlices = 5
        lonList = np.linspace(swLon, neLon, numLonSlices, endpoint=True)
        numLons = len(lonList)-1

        #print(str(numFourSquareCalls) + ' ' + str(swLat))
        for nWhichSWLat in range(numSWLats):
            swLat = swLatList[nWhichSWLat]

            #print('{}'.format(nWhichSWLat))

            for nWhichSWLon in range(numLons):
                # Make sure the longitudes overlap a little; do this by
                # making swLon a little more negative
                swLon = lonList[nWhichSWLon] - 0.0005
                neLon = lonList[nWhichSWLon+1]
                
                #print('{},{} {},{}  {},{}'.format(nWhichSWLat, nWhichSWLon, swLat, swLon, neLat, neLon))

                url = 'https://api.foursquare.com/v2/venues/search?intent=browse&client_id={}&client_secret={}&sw={},{}&ne={},{}&v={}&categoryId={}&limit={}'\
    .format(CLIENT_ID, CLIENT_SECRET, swLat, swLon, neLat, neLon, VERSION, categoryID, LIMIT)
                numFourSquareCalls = numFourSquareCalls + 1
                #print(url)
                results = requests.get(url).json()
                httpResponseCode = results['meta']['code']
                if (httpResponseCode == 429):
                    print('*** Exceeded FourSquare API call quota after ' + str(numFourSquareCalls) + ' calls ***')

                # assign relevant part of JSON to venues
                venues = results['response']['venues']
#       print(len(venues))

                # tranform venues into a dataframe
                dfOneRect = json_normalize(venues)
                dfOneRect['category'] = categoryName
                numVenuesInRect = dfOneRect.shape[0]
                if (numVenuesInRect >= 50):
                    print('Retrieved the maximum number of venues {} for category {} with SW latitude {} url {} numLatSlices {}'.format(numVenuesInRect, categoryName, swLat, url, numLatSlices))

                numVenuesRetrieved = numVenuesRetrieved + numVenuesInRect
                if (numVenuesRetrieved - numRoundedVenuesRetrieved >= 100):
                    numRoundedVenuesRetrieved = round(numVenuesRetrieved, -2)
                    print("Retrieved {} venues".format(numRoundedVenuesRetrieved))

                #print('Retrieved ' + str(dfOneRect.shape[0]) + ' for category ' + categoryName + ' with SW latitude ' + str(swLat))
                #print()
                # append that dataframe to the one containing all rectangles' venues
                dfAllVenues = pd.concat([dfAllVenues, dfOneRect], sort=False)
        
# Drop the columns other than the ones listed in the next line
dfAllVenues.drop(dfAllVenues.columns.difference(['id', 'category', 'name', 'location.postalCode', \
                                'location.address', 'location.city', 'location.lat', 'location.lng']), 1, inplace=True)

newColumnNames = ['category', 'id', 'address', 'city', 'lat', 'lon', 'zip', 'name']
dfAllVenues.columns = newColumnNames
dfAllVenues.columns
## Drop rows where the venue doesn't have a zip code, because we need that for further processing
#dfAllVenues.dropna(subset=['location.postalCode'], inplace=True)
#dfAllVenues.shape
print('numFourSquareCalls=' + str(numFourSquareCalls))
#print(dfAllVenues.shape)

# We will have received duplicate venues because our lat/lon rectangles overlap,
# and also because FourSquare rounds the lat/lon values to only a few digits.
# Let's eliminate the duplicate rows
#numRowsWithDups = len(dfAllVenues)
#dfAllVenues.drop_duplicates(keep=first, inplace=True) 
#numRowsWithoutDups = len(dfAllVenues)
#print('Dropped {} duplicate venues, {} venues remain'.format(numRowsWithDups-numRowsWithoutDups, numRowsWithoutDups))
dfAllVenues.head()

Retrieving Mexican Restaurant
Retrieved 100 venues
Retrieved 200 venues
Retrieved 300 venues
Retrieved 400 venues
Retrieved 500 venues
Retrieved 600 venues
Retrieved 700 venues
Retrieved 800 venues
Retrieved 900 venues
Retrieved the maximum number of venues 50 for category Mexican Restaurant with SW latitude 40.636756 url https://api.foursquare.com/v2/venues/search?intent=browse&client_id=UYWTHYG53L3ENHJ4O50HDEHZKE51X0NPSR3YCXC1I0JCDGRA&client_secret=OPBF0AHVEAL11QB0HZUIWHP2BAUWQLZY4U0ZF10USQQVF0PJ&sw=40.636756,-74.00459375000001&ne=40.678819,-73.9600195&v=20180604&categoryId=4bf58dd8d48988d1c1941735&limit=50 numLatSlices 1
Retrieved 1000 venues
Retrieved 1100 venues
Retrieved 1200 venues
Retrieving Jazz Club
Retrieved 100 venues
numFourSquareCalls=1241


category                        id            address      city  \
0  Mexican Restaurant  4a807ab1f964a52067f51fe3  2 Broadway Frnt 4  New York   
1  Mexican Restaurant  5bc7421f00b068002df2320a  1 State St         New York   
2  Mexican Restaurant  5a9f251b8496ca36c46114ab  15 Stone St        New York   
3  Mexican Restaurant  4a524983f964a5207fb11fe3  85 Greenwich St    New York   
4  Mexican Restaurant  513f6223e4b0ddc812b16c87  69 New St          New York   

         lat        lon    zip                    name  
0  40.704888 -74.012846  10004  Chipotle Mexican Grill  
1  40.702289 -74.013072  10004  Dos Toros               
2  40.704053 -74.012071  10004  Toro Loco               
3  40.707778 -74.013507  10006  Tajin                   
4  40.705548 -74.012208  10004  El Toro

In [126]:
pd.set_option('display.max_rows', 1000)
print(len(dfAllVenues['zip'].unique()))
print(len(dfAllVenues))
print(dfAllVenues['zip'].unique())


75
638
['10004' '10005' '10041' nan '10038' '10282' '10011' '10013' '10002'
 '10007' '10012' '10036' '10009' '10014' '10003' '10023' '10010' '10016'
 '11237' '10001' '10018' '10017' '10019' '10022' '10065' '10021' '10111'
 '10020' '10103' '10573' 'Vr' '10028' '10128' '10024' '10029' '10025'
 '10026' '10035' '10027' '10030' '10031' '10033' '11220' '11209' '11218'
 '11204' '11214' '11223' '11219' '11230' '11210' '11229' '11234' '11236'
 '07307' '11215' '11231' '11225' '11238' '11226' '11213' '11212' '11207'
 '11208' '11201' '11217' '11205' '11206' '11216' '11221' '11233' '11385'
 '11222' '11249' '10032']


In [127]:
dfAllVenues.columns

Index(['category', 'id', 'address', 'city', 'lat', 'lon', 'zip', 'name'], dtype='object')

In [200]:
# Some results from FourSquare have lat/lon, but no zip code
# Use reverse geocoding from Bing to retrieve the missing zip codes,
# and update dfAllVenues

allVenuesCleanList = []
dfNoZip = dfAllVenues[dfAllVenues['zip'].isna()]

print("Before processing, there are " + str(len(dfNoZip)) + " rows in dfAllVenues without zip codes")

# Ensure that zip code is a string
dfAllVenues.zip = dfAllVenues.zip.astype(str)

# Get the column index of 'zip' so we can use the faster "iat" method
zipIndex = dfAllVenues.columns.get_loc("zip")+1

numZipsChanged = 0
#for index, row in dfNoZip.iterrows():    
for index, row in dfAllVenues.iterrows():
    #print(row[zipIndex] == 'nan')
    try:
        theCategory = row.category
        theID = row['id']
        theAddress = row['address']
        theCity = row['city']
        theLat = row['lat']
        theLon = row['lon']
        theZip = row['zip']
        theName = row['name']
        bUpdateZip = theZip == 'nan' or (len(str(theZip)) != 5)
        if (bUpdateZip):
            numZipsChanged = numZipsChanged + 1
            lat = row['lat']
            lon = row['lon']
            bingURL = 'https://dev.virtualearth.net/REST/v1/locationrecog/{},{}?key={}&r=.5&distanceUnit=mi&includeEntityTypes=address&output=json'\
            .format(lat,lon,bingMapsKey)

            #print('Zip is "{}" for {} {}, {}'.format(row.zip, index, lat, lon))

            results = requests.get(bingURL).json()
            theZip = results['resourceSets'][0]['resources'][0]['addressOfLocation'][0]['postalCode']
#            print('Changing zip from "{}" to {} for {}, {}'.format(row.zip, theZip, lat, lon))
        
            #dfAllVenues.set_value(index, 'zip', theZip)
            #row['zip'] = theZip
            #dfAllVenues.at[row.index, 'zip'] = theZip
            #print(' Now {}'.format(dfAllVenues.at[index, 'zip']))
            
#        print(row['name'])
        rowData = [theCategory, theID, theAddress, theCity, theLat, theLon, theZip, theName]
        allVenuesCleanList.append(rowData)

#    except:
    except Exception as e: 
        pass # doing nothing on exception, we'll filter out rows w/o zip codes later
        print(e)
    
# Now repeat for empty string zip codes
#dfNoZip = dfAllVenues[dfAllVenues['zip'].str.len().eq(0)]
##for index, row in dfNoZip.iterrows():    
#for row in dfAllVenues.itertuples():
#    try:
#        if (row['zip'].isna()):
#            lat = row.lat
#            lon = row.lon
#            bingURL = 'https://dev.virtualearth.net/REST/v1/locationrecog/{},{}?key={}&r=.5&distanceUnit=mi&includeEntityTypes=address&output=json'\
#            .format(lat,lon,bingMapsKey)
#
#            results = requests.get(bingURL).json()
#            theZip = results['resourceSets'][0]['resources'][0]['addressOfLocation'][0]['postalCode']
#            dfAllVenues.at[index, 'zip'] = theZip
#
#            #print('Zip is {} for {}, {}'.format(theZip, lat, lon))
#    except:
##        print(results)
#        pass # doing nothing on exception, we'll filter out rows w/o zip codes later

dfAllVenuesClean = pd.DataFrame(allVenuesCleanList)
newColumnNames = ['category', 'id', 'address', 'city', 'lat', 'lon', 'zip', 'name']
dfAllVenuesClean.columns = newColumnNames

#dfNoZip = dfAllVenues[dfAllVenues['zip'].isna()]
#dfNoZip2 = dfAllVenues[dfAllVenues['zip'].str.len().eq(0)]
print("Fixed {} zip codes".format(numZipsChanged))

# Ensure that zip code is a string
#dfAllVenues.zip = dfAllVenues.zip.astype(str)
#dfAllVenues.head()
dfAllVenuesClean.head()

Before processing, there are 130 rows in dfAllVenues without zip codes
Fixed 130 zip codes


category                        id            address      city  \
0  Mexican Restaurant  4a807ab1f964a52067f51fe3  2 Broadway Frnt 4  New York   
1  Mexican Restaurant  5bc7421f00b068002df2320a  1 State St         New York   
2  Mexican Restaurant  5a9f251b8496ca36c46114ab  15 Stone St        New York   
3  Mexican Restaurant  4a524983f964a5207fb11fe3  85 Greenwich St    New York   
4  Mexican Restaurant  513f6223e4b0ddc812b16c87  69 New St          New York   

         lat        lon    zip                    name  
0  40.704888 -74.012846  10004  Chipotle Mexican Grill  
1  40.702289 -74.013072  10004  Dos Toros               
2  40.704053 -74.012071  10004  Toro Loco               
3  40.707778 -74.013507  10006  Tajin                   
4  40.705548 -74.012208  10004  El Toro

In [201]:
print(dfAllVenuesClean.columns)

Index(['category', 'id', 'address', 'city', 'lat', 'lon', 'zip', 'name'], dtype='object')


In [202]:
#newColumnNames = ['category', 'id', 'address', 'city', 'lat', 'lon', 'zip', 'name']
#dfAllVenuesClean.columns = newColumnNames
#dfAllVenuesClean.head()
print(len(dfAllVenuesClean['zip'].unique()))
print(len(dfAllVenuesClean))
print(dfAllVenuesClean['zip'].unique())

93
1378
['10004' '10006' '10005' '10041' '10038' '10282' '10080' '10280' '10007'
 '10281' '10012' '32811' '10013' '10002' '21312' '10009' '10001' '11211'
 '10003' '10024' '10459' '10014' '10011' '10010' '07310' '10016' '07102'
 '10119' '10018' '10121' '10036' '11220' '10118' '10017' '10022' '10169'
 '10167' '10019' '10020' '10104' '10103' '10065' '10021' '10023' '11370'
 '10075' '10028' '10128' '10025' '10029' '10035' '10026' '10027' '10031'
 '10037' '10039' '10032' '10033' '10034' '10040' '11209' '11214' '11228'
 '11223' '11219' '11230' '11204' '11218' '11229' '11210' '11226' '11234'
 '11236' '11232' '11215' '11217' '11238' '11225' '11231' '11216' '11203'
 '11233' '11207' '11201' '11205' '11206' '11221' '11237' '11385' '11222'
 '11249' '11378' '10030']


In [203]:
dfAllVenues = dfAllVenuesClean
print(dfAllVenues['zip'].unique())

['10004' '10006' '10005' '10041' '10038' '10282' '10080' '10280' '10007'
 '10281' '10012' '32811' '10013' '10002' '21312' '10009' '10001' '11211'
 '10003' '10024' '10459' '10014' '10011' '10010' '07310' '10016' '07102'
 '10119' '10018' '10121' '10036' '11220' '10118' '10017' '10022' '10169'
 '10167' '10019' '10020' '10104' '10103' '10065' '10021' '10023' '11370'
 '10075' '10028' '10128' '10025' '10029' '10035' '10026' '10027' '10031'
 '10037' '10039' '10032' '10033' '10034' '10040' '11209' '11214' '11228'
 '11223' '11219' '11230' '11204' '11218' '11229' '11210' '11226' '11234'
 '11236' '11232' '11215' '11217' '11238' '11225' '11231' '11216' '11203'
 '11233' '11207' '11201' '11205' '11206' '11221' '11237' '11385' '11222'
 '11249' '11378' '10030']


### Read in Zip Codes

In [204]:
# Read in the CSV file 'Brooklyn and Manhattan Zip Codes By Neighborhood.csv'.
# I created this file by combining data from several files. The CSV file
# has these columns:
#  Borough: Either Brooklyn or Manhattan
#  SubBoroNumber: An identifier created by New York City to identify sections of each borough
#  Name: The name of the neighborhood(s) (sub-boro)
#  ZipCode: One of the zip codes in the neighborhood(s)
# There are multiples lines for most neighborhoods in the CSV file, because
# most neighborhoods contain more than one zip code

import io

wrapper = io.TextIOWrapper(project.get_file("Brooklyn and Manhattan Zip Codes By Neighborhood.csv"), encoding='utf-8')
dfNeighborhoodZipcodes = pd.read_csv(wrapper)

# Lets convert ZipCode from int to string, so that zips with leading zeroes (e.g., 02123) work.
# NYC doesn't have any zips with leading zeroes, but it's good data management
# to ensure that code will work with any valid data that's out there, not just the 
# particular data you're using at the moment
dfNeighborhoodZipcodes.ZipCode = dfNeighborhoodZipcodes.ZipCode.astype(str)

# Ensure that Borough and Name columns are strings
dfNeighborhoodZipcodes.Borough = dfNeighborhoodZipcodes.Borough.astype(str)
dfNeighborhoodZipcodes.Name = dfNeighborhoodZipcodes.Name.astype(str)

# Let's test our int-to-string conversion by checking which neighborhood the 
# zip code "11201" (a string, not the int 11201) is in
print(dfNeighborhoodZipcodes.loc[dfNeighborhoodZipcodes['ZipCode'] == "11201"])

    Borough  SubBoroNumber                           Name ZipCode
2  Brooklyn  2              Brooklyn Heights, Fort Greene  11201 


In [205]:
# Read in a CSV file that has the population of each neighborhood
# The CSV file has these columns:
#  Borough: Either Brooklyn or Manhattan
#  SubBoroNumber: An identifier created by New York City to identify sections of each borough
#  Name: The name of the neighborhood(s) (sub-boro)
#  Population: The number of people living in the neighborhood as of the 2010 census
#  Rent: The median rent for a 1-bedroom apartment
# We can match rows in this data to rows in the zip code file by matching Borough andSubBohoNumber,
# or more directly by matching the neighborhood name

wrapper = io.TextIOWrapper(project.get_file("Brooklyn and Manhattan Population And Rent By Neighborhood.csv"), encoding='utf-8')
dfNeighborhoodPopulation = pd.read_csv(wrapper)
dfNeighborhoodPopulation.head()

Borough  SubBoroNumber                           Name  Population  Rent
0  Brooklyn  1              Williamsburg, Greenpoint       173083      2720
1  Brooklyn  2              Brooklyn Heights, Fort Greene  99617       2975
2  Brooklyn  3              Bedford Stuyvesant             152985      2200
3  Brooklyn  4              Bushwick                       112634      2200
4  Brooklyn  5              East New York, Starrett City   182896      1375

In [206]:
# Now that we have the venues (with zip codes), and a way to look up
# a neighborhood for a particular zip code, iterate over dfAllVenues,
# adding the neighborhood to each entry.

# Start by adding the columns that exist in dfNeighborhoodZipcodes to dfAllVenues
dfAllVenues["Borough"] = ""
dfAllVenues["SubBoroNumber"] = 0
dfAllVenues["Neighborhood"] = ""

numRowsProcessed = 0
numVenuesRemoved = 0
for index, row in dfAllVenues.iterrows():    
    numRowsProcessed = numRowsProcessed + 1

    zipCode = row.zip
    name = row.name
    
    # Get the neighborhood this zip code corresponds to
    dfNeighborhood = dfNeighborhoodZipcodes.loc[dfNeighborhoodZipcodes['ZipCode'] == zipCode]
    if (len(dfNeighborhood) == 0):
        numVenuesRemoved = numVenuesRemoved + 1
#        print("No neighborhood for zip code " + zipCode + " for venue " + name)
        print("No neighborhood for zip code '" + zipCode + "'")
    else:
        borough = dfNeighborhood.iloc[0]["Borough"]
        subBoro = dfNeighborhood.iloc[0]["SubBoroNumber"]
        neighborhood = dfNeighborhood.iloc[0]["Name"]

        dfAllVenues.at[index, 'Borough'] = borough
        dfAllVenues.at[index, 'SubBoroNumber'] = subBoro
        dfAllVenues.at[index, 'Neighborhood'] = neighborhood
        dfAllVenues.at[index, 'ZipCode'] = zipCode
        dfAllVenues.at[index, 'Name'] = name
#        if (zipCode == "11238"):
#            print(neighborhood)

print("{} venues processed, {} removed".format(numRowsProcessed, numVenuesRemoved))
dfAllVenues.head()

No neighborhood for zip code '32811'
No neighborhood for zip code '21312'
No neighborhood for zip code '21312'
No neighborhood for zip code '10459'
No neighborhood for zip code '10459'
No neighborhood for zip code '07310'
No neighborhood for zip code '07102'
No neighborhood for zip code '10119'
No neighborhood for zip code '10121'
No neighborhood for zip code '10167'
No neighborhood for zip code '10104'
No neighborhood for zip code '10103'
No neighborhood for zip code '11370'
No neighborhood for zip code '11385'
No neighborhood for zip code '11385'
No neighborhood for zip code '11385'
No neighborhood for zip code '11385'
No neighborhood for zip code '11385'
No neighborhood for zip code '11249'
No neighborhood for zip code '11378'
No neighborhood for zip code '11378'
1378 venues processed, 21 removed


category                        id            address      city  \
0  Mexican Restaurant  4a807ab1f964a52067f51fe3  2 Broadway Frnt 4  New York   
1  Mexican Restaurant  5bc7421f00b068002df2320a  1 State St         New York   
2  Mexican Restaurant  5a9f251b8496ca36c46114ab  15 Stone St        New York   
3  Mexican Restaurant  4a524983f964a5207fb11fe3  85 Greenwich St    New York   
4  Mexican Restaurant  513f6223e4b0ddc812b16c87  69 New St          New York   

         lat        lon    zip                    name    Borough  \
0  40.704888 -74.012846  10004  Chipotle Mexican Grill  Manhattan   
1  40.702289 -74.013072  10004  Dos Toros               Manhattan   
2  40.704053 -74.012071  10004  Toro Loco               Manhattan   
3  40.707778 -74.013507  10006  Tajin                   Manhattan   
4  40.705548 -74.012208  10004  El Toro                 Manhattan   

   SubBoroNumber                Neighborhood ZipCode  Name  
0  1              Battery Park City, Tribeca  10004   0.0   
1  1              Battery Park City, Tribeca  10004   1.0   
2  1              Battery Park City, Tribeca  10004   2.0   
3  1              Battery Park City, Tribeca  10006   3.0   
4  1              Battery Park City, Tribeca  10004   4.0

In [207]:
dfAllVenues['zip'].unique()

array(['10004', '10006', '10005', '10041', '10038', '10282', '10080',
       '10280', '10007', '10281', '10012', '32811', '10013', '10002',
       '21312', '10009', '10001', '11211', '10003', '10024', '10459',
       '10014', '10011', '10010', '07310', '10016', '07102', '10119',
       '10018', '10121', '10036', '11220', '10118', '10017', '10022',
       '10169', '10167', '10019', '10020', '10104', '10103', '10065',
       '10021', '10023', '11370', '10075', '10028', '10128', '10025',
       '10029', '10035', '10026', '10027', '10031', '10037', '10039',
       '10032', '10033', '10034', '10040', '11209', '11214', '11228',
       '11223', '11219', '11230', '11204', '11218', '11229', '11210',
       '11226', '11234', '11236', '11232', '11215', '11217', '11238',
       '11225', '11231', '11216', '11203', '11233', '11207', '11201',
       '11205', '11206', '11221', '11237', '11385', '11222', '11249',
       '11378', '10030'], dtype=object)

In [208]:
print(len(dfAllVenues['zip'].unique()))

93


In [209]:
# Clean up the data, removing any rows in dfAllVenues that have SubBoroNumber == 0, because
# that means their zip code did not match up with any of the zip codes in the neighborhoods
# we're including.
numRowsBefore = len(dfAllVenues)

# Get indexes for which column SubBoroNumber is zero
indexNames = dfAllVenues[dfAllVenues['SubBoroNumber'] == 0].index
 
# Delete these row indexes from dataFrame
dfAllVenues.drop(indexNames , inplace=True)
numRowsAfter = len(dfAllVenues)
numRowsRemoved = numRowsBefore - numRowsAfter
print("Removed " + str(numRowsRemoved) + " rows that are in neighborhoods we're not including")


Removed 21 rows that are in neighborhoods we're not including


In [94]:
## Debug
dfAllVenues.loc[dfAllVenues['zip'] == "10021"]

category                        id              address      city  \
195  Movie Theater  4e3985e2bd418bd4ba44d17e  10 East 66th Street  New York   
231  Movie Theater  4f00bdbfa69d45461e69c508                  NaN  New York   
233  Movie Theater  4ebc62d06da1d1ac280bc6f3        1170 2nd Ave.  New York   
249  Movie Theater  52b71292498e43b4dc0ff489                  NaN  New York   
250  Movie Theater  52ca265c11d2dc18de71be6e                  NaN  New York   
252  Movie Theater  52ca25f2498e3a32e6fae696                  NaN  New York   
254  Movie Theater  50dce751e4b04b9246f60656                  NaN  New York   
255  Movie Theater  52ca25f2498e3a32e6fae696                  NaN  New York   
280  Movie Theater  4fb4762fe4b0186ba36db69d                  NaN  New York   
572      Jazz Club  3fd66200f964a520ede71ee3         35 E 76th St  New York   
573      Jazz Club  4fb03a2ce4b047f11dc5104c                  NaN  New York   
576      Jazz Club  3fd66200f964a520ede71ee3         35 E 76th St  New York   

           lat        lon    zip  name    Borough  SubBoroNumber  \
195  40.768210 -73.968772  10021    10  Manhattan              8   
231  40.767205 -73.960817  10021     9  Manhattan              8   
233  40.763078 -73.962011  10021    11  Manhattan              8   
249  40.772437 -73.962582  10021     0  Manhattan              8   
250  40.771734 -73.962585  10021     1  Manhattan              8   
252  40.771798 -73.962327  10021     3  Manhattan              8   
254  40.772633 -73.953476  10021     0  Manhattan              8   
255  40.771798 -73.962327  10021     1  Manhattan              8   
280  40.786754 -73.972084  10021     2  Manhattan              8   
572  40.774466 -73.963369  10021     0  Manhattan              8   
573  40.772670 -73.959870  10021     0  Manhattan              8   
576  40.774466 -73.963369  10021     0  Manhattan              8   

        Neighborhood ZipCode  
195  Upper East Side   10021  
231  Upper East Side   10021  
233  Upper East Side   10021  
249  Upper East Side   10021  
250  Upper East Side   10021  
252  Upper East Side   10021  
254  Upper East Side   10021  
255  Upper East Side   10021  
280  Upper East Side   10021  
572  Upper East Side   10021  
573  Upper East Side   10021  
576  Upper East Side   10021

In [210]:
#dfAllVenues.groupby(['Borough', 'SubBoroNumber'], axis=1).name.agg('count').to_frame('VenueCount')
dfAllVenues.groupby(['Borough', 'SubBoroNumber']).name.agg('count').to_frame('VenueCount')

VenueCount
Borough   SubBoroNumber            
Brooklyn  1              13        
          2              49        
          3              25        
          4              72        
          5              4         
          6              41        
          7              26        
          8              8         
          10             24        
          11             15        
          12             28        
          13             13        
          14             11        
          15             5         
          17             5         
          18             15        
Manhattan 1              137       
          2              240       
          3              68        
          4              112       
          5              54        
          6              35        
          7              83        
          8              68        
          9              30        
          10             33        
          11             67        
          12             76

In [96]:
## Debvug
dfAllVenues.groupby(['Borough', 'SubBoroNumber']).name.agg('count').to_frame('VenueCount')

VenueCount
Borough   SubBoroNumber            
Brooklyn  1                       5
          2                      26
          3                       6
          4                      22
          5                       5
          6                      26
          7                       4
          8                       4
          9                       1
          10                      5
          11                      2
          12                      9
          13                      3
          14                      8
          15                      3
          16                      1
          17                      9
          18                     13
Manhattan 1                      75
          2                      85
          3                      38
          4                     100
          5                      33
          6                      12
          7                      57
          8                      28
          9                       2
          10                     31
          11                      3
          12                     12

In [211]:
# Create a new dataframe that has the borough, sub-boro, and the groupby count
# of venues in that borough/sub-boro
#dfVenueCount = dfAllVenues.groupby(['Borough', 'SubBoroNumber']).name.agg('count').to_frame('VenueCount').reset_index()
dfVenueCount = dfAllVenues.groupby(['Borough', 'SubBoroNumber']).name.agg('count').to_frame('VenueCount')

In [212]:
dfVenueCount

VenueCount
Borough   SubBoroNumber            
Brooklyn  1              13        
          2              49        
          3              25        
          4              72        
          5              4         
          6              41        
          7              26        
          8              8         
          10             24        
          11             15        
          12             28        
          13             13        
          14             11        
          15             5         
          17             5         
          18             15        
Manhattan 1              137       
          2              240       
          3              68        
          4              112       
          5              54        
          6              35        
          7              83        
          8              68        
          9              30        
          10             33        
          11             67        
          12             76

In [213]:
venueHoods = dfAllVenues['Neighborhood'].unique()
print("{} neighborhoods out of {} have venues".format(len(venueHoods), len(dfNeighborhoodPopulation)))
#
print("Here are the neighborhoods with no venues: ")
#allHoods = dfNeighborhoodPopulation['Name'].unique()
print(dfNeighborhoodPopulation.loc[(~dfNeighborhoodPopulation['Name'].isin(venueHoods))]['Name'])

28 neighborhoods out of 30 have venues
Here are the neighborhoods with no venues: 
8     Crown Heights South, Wingate
15    Brownsville, Ocean Hill     
Name: Name, dtype: object


In [214]:
# Merge the two dataframes: dfNeighborhoodPopulation and dfVenueCount
# They both have a Borough and a SubBoroNumber column, so we'll merge
# on that combination. We'll do a left merge, which will include all
# the columns from dfNeighborhoodPopulation, and add the VenueCount
# column
dfNeighborhoodPopulation = pd.merge(dfNeighborhoodPopulation, dfVenueCount, how='left', on =['Borough', 'SubBoroNumber'])

#dfNeighborhoodPopulation.VenueCount = dfNeighborhoodPopulation.VenueCount.astype(int)

dfNeighborhoodPopulation.head()

Borough  SubBoroNumber                           Name  Population  Rent  \
0  Brooklyn  1              Williamsburg, Greenpoint       173083      2720   
1  Brooklyn  2              Brooklyn Heights, Fort Greene  99617       2975   
2  Brooklyn  3              Bedford Stuyvesant             152985      2200   
3  Brooklyn  4              Bushwick                       112634      2200   
4  Brooklyn  5              East New York, Starrett City   182896      1375   

   VenueCount  
0  13.0        
1  49.0        
2  25.0        
3  72.0        
4  4.0

In [215]:
dfPop = dfNeighborhoodPopulation

# A neighborhood that doesn't have any venues will have NaN for VenueCount.
# Convert those to zero
values = {'VenueCount': 0}
dfPop.fillna(value=values, inplace=True)

# Calculate the number of venues per 10,000 residents of each neighborhood
dfPop["VenueDensity"] = dfNeighborhoodPopulation["VenueCount"] / (dfNeighborhoodPopulation["Population"] / 10000)

# Print the neighborhoods with the highest venue densities
dfPop = dfPop.sort_values('VenueDensity', ascending=False)

dfPop.head(10)

Borough  SubBoroNumber                           Name  Population  Rent  \
19  Manhattan  2              Greenwich Village, Soho        90016       3375   
18  Manhattan  1              Battery Park City, Tribeca     60978       3877   
21  Manhattan  4              Chelsea, Clinton               103245      3700   
22  Manhattan  5              Midtown Business District      51673       3125   
3   Brooklyn   4              Bushwick                       112634      2200   
28  Manhattan  11             East Harlem                    120511      2145   
1   Brooklyn   2              Brooklyn Heights, Fort Greene  99617       2975   
20  Manhattan  3              Lower East Side, Chinatown     163277      2950   
29  Manhattan  12             Washington Heights, Inwood     190020      1775   
24  Manhattan  7              West Side, Upper West Side     209084      3150   

    VenueCount  VenueDensity  
19  240.0       26.661927     
18  137.0       22.467119     
21  112.0       10.847983     
22  54.0        10.450332     
3   72.0        6.392386      
28  67.0        5.559658      
1   49.0        4.918839      
20  68.0        4.164702      
29  76.0        3.999579      
24  83.0        3.969696

## Geopandas

In [216]:
pd.set_option('display.max_colwidth', -1)
pd.set_option('display.max_rows', 20)

In [217]:
import geopandas as gpd

# Read the zip code/boundary file into memory
nyBoundaryFile = project.get_file('NYCZipcodeBoundaries.json')

# Turn the zip code/boundary file into a geopandas dataframe
nyBoundaries = gpd.read_file(nyBoundaryFile)
nyBoundaries.head()

# select the columns that you with to use for the dissolve and that will be retained
nyBoundaries2 = nyBoundaries[['postalCode', 'borough', 'PO_NAME', 'geometry']]
#print(nyBoundaries2['PO_NAME'] + "  " + nyBoundaries2['postalCode'])


In [218]:
# Drop the rows from the geojson file that are for zip code we aren't using
nyBoundaries2 = nyBoundaries2[nyBoundaries2.postalCode.isin(dfNeighborhoodZipcodes['ZipCode'])]
nyBoundaries2.head()

postalCode   borough   PO_NAME  \
21  11221      Brooklyn  Brooklyn   
25  11216      Brooklyn  Brooklyn   
27  11233      Brooklyn  Brooklyn   
29  11213      Brooklyn  Brooklyn   
30  11212      Brooklyn  Brooklyn   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         geometry  
21  POLYGON ((-73.93822325191614 40.68389331961758, -73.9438911382472 40.68323950227984, -73.94564165707669 40.69203346946512, -73.93413376737952 40.69335436373854, -73.93479698827541 40.69673661671486, -73.9352226413318 40.69698656384033, -73.93226765371799 40.69731469442813, -73.93324668417745 40.69785561272368, -73.93076911862683 40.69891104645372, -73.9305202888139 40.69877230313472, -73.92758773780713 40.70176259998695, -73.92308168149715 40.69920069630066, -73.92163115701487 40.70067558024493, -73.92087956801677 40.70024736678035, -73.92232800953694 40.6987721198053, -73.91848721378724 40.69658602292844, -73.91781911962863 40.69620772862452, -73.91636718052304 40.69768090418263, -73.90885282871758 40.69340445130968, -73.91604598744264 40.68607208871235, -73.91804606753695 40.687213268776, -73.9178493642506 40.68623318739356, -73.93822325191614 40.68389331961758))  
25  POLYGON ((-73.94564165707669 40.69203346946512, -73.9438911382472 40.68323950227984, -73.93822325191614 40.68389331961758, -73.93739763108535 40.67972992244106, -73.94120864001327 40.67993836946285, -73.94160931928725 40.67564320442343, -73.94714602322288 40.67594438109577, -73.94773123647958 40.6697047078836, -73.9550528799369 40.67010365000868, -73.95797316022487 40.6706572921663, -73.95516306696332 40.67852074712599, -73.95713186042737 40.68846315202325, -73.95131871695537 40.68913231750482, -73.95175746790927 40.69132933067435, -73.94564165707669 40.69203346946512))                                                                                                                                                                                                                                                                                                               
27  POLYGON ((-73.93822325191614 40.68389331961758, -73.9178493642506 40.68623318739356, -73.91804606753695 40.687213268776, -73.9034668872538 40.67889653817026, -73.90329155804092 40.67786792438706, -73.90346256333866 40.6760158063333, -73.90240783422718 40.67587541049135, -73.90438871964855 40.67517137038907, -73.925653595542 40.66582990624871, -73.92580501111077 40.666456157208, -73.92499590519674 40.67473589594239, -73.92776143466391 40.67488742035348, -73.92768791018021 40.67566288431892, -73.93045708472673 40.67581876680987, -73.93020074773672 40.67804022252579, -73.92905727071383 40.67927645406513, -73.93739763108535 40.67972992244106, -73.93822325191614 40.68389331961758))                                                                                                                                                                                                  
29  POLYGON ((-73.93739763108535 40.67972992244106, -73.92905727071383 40.67927645406513, -73.93020074773672 40.67804022252579, -73.93045708472673 40.67581876680987, -73.92768791018021 40.67566288431892, -73.92776143466391 40.67488742035348, -7

In [219]:
# Now merge the neighborhood column from dfNeighborhoodZipcodes into nyBoundaries2, matching on zip code

# First, let's change 'postalCode' to 'ZipCode' since that's what dfNeighborhoodZipcodes calls it
newColumnNames = list(nyBoundaries2.columns)
for idx, item in enumerate(newColumnNames):
   if 'postalCode' in item:
       newColumnNames[idx] = 'ZipCode'
nyBoundaries2.columns = newColumnNames

nyBoundaries2 = pd.merge(nyBoundaries2, dfNeighborhoodZipcodes, how='inner', on =['ZipCode'])

# dissolve the state boundary by region 
nyBoundaries3 = nyBoundaries2.dissolve(by='Name')

# Turn the Name column from an index back into a regular column we can access
nyBoundaries3.reset_index(inplace=True)

print("Merged the geographic boundaries of " + str(len(nyBoundaries2)) + " zip codes into " + str(len(nyBoundaries3)) + " neighborhoods")

# We have to add the neighborhood name back into nyBoundaries3. It was
# lost during the dissolve
#nyBoundaries3['Neighborhood'] = dfNeighborhoodZipcodes.loc[dfNeighborhoodZipcodes['ZipCode'] == nyBoundaries3.iloc[0]['ZipCode']].Name


Merged the geographic boundaries of 97 zip codes into 30 neighborhoods


## Maps

In [220]:
# Get the lat/lon of the center of Manhattan & Brooklyn
# I visually determind the 'center' of Manhattan to be about where the Guggenheim Museum is,
# just east of Central Park, so I query Bing to get its lat/lon
bingURL = 'http://dev.virtualearth.net/REST/v1/Locations/{}?maxResults=1&key={}'.format("Guggenheim Museum, NY", bingMapsKey)
results = requests.get(bingURL).json()
manhattanCenter = results['resourceSets'][0]['resources'][0]['geocodePoints'][0]['coordinates']
print("Manhattan center: " + str(manhattanCenter))

# Various online sources pinpoint the center of Brookly as Brooklyn College, which is at
# 2900 Bedford Avenue.
bingURL = 'http://dev.virtualearth.net/REST/v1/Locations/{}?maxResults=1&key={}'.format("2900 Bedford Avenue, Brookly, NY", bingMapsKey)
results = requests.get(bingURL).json()
brooklynCenter = results['resourceSets'][0]['resources'][0]['geocodePoints'][0]['coordinates']
print("Brooklyn center: " + str(brooklynCenter))


Manhattan center: [40.78292465209961, -73.95895385742188]
Brooklyn center: [40.631289, -73.952159]


In [221]:
def neighborhoods_style(feature):
    return { 'color': 'blue', 'fill': False }

In [108]:
# NOTE: This takes a long time
#%%capture
!conda install -c conda-forge folium

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    altair-3.2.0               |           py36_0         770 KB  conda-forge
    certifi-2019.9.11          |           py36_0         147 KB  conda-forge
    openssl-1.1.1c             |       h516909a_0         2.1 MB  conda-forge
    vincent-0.4.4              |             py_1          28 KB  conda-forge
    folium-0.10.0              |             py_0          59 KB  conda-forge
    branca-0.3.1               |             py_0          25 KB  conda-forge
    ca-certificates-2019.9.11  |       hecc5488_0         144 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         3.3 MB

The following NEW packages will be INSTAL

In [222]:
import folium
from folium import plugins
from folium.plugins import HeatMap

map_manhattan = folium.Map(location=manhattanCenter, zoom_start=13, tiles='Mapbox Bright')
folium.TileLayer('cartodbpositron').add_to(map_manhattan)
#HeatMap(restaurant_latlons).add_to(map_berlin)
#folium.Marker(manhattanCenter).add_to(map_manhattan)
#folium.Circle(manhattanCenter, radius=1000, fill=False, color='white').add_to(map_berlin)
#folium.Circle(manhattanCenter, radius=2000, fill=False, color='white').add_to(map_berlin)
#folium.Circle(manhattanCenter, radius=3000, fill=False, color='white').add_to(map_berlin)
gjson = nyBoundaries3.to_crs(epsg='4326').to_json()
folium.GeoJson(gjson, style_function=neighborhoods_style, name='geojson').add_to(map_manhattan)
#map_manhattan

In [223]:
dfAllVenues.head()

category                        id            address      city  \
0  Mexican Restaurant  4a807ab1f964a52067f51fe3  2 Broadway Frnt 4  New York   
1  Mexican Restaurant  5bc7421f00b068002df2320a  1 State St         New York   
2  Mexican Restaurant  5a9f251b8496ca36c46114ab  15 Stone St        New York   
3  Mexican Restaurant  4a524983f964a5207fb11fe3  85 Greenwich St    New York   
4  Mexican Restaurant  513f6223e4b0ddc812b16c87  69 New St          New York   

         lat        lon    zip                    name    Borough  \
0  40.704888 -74.012846  10004  Chipotle Mexican Grill  Manhattan   
1  40.702289 -74.013072  10004  Dos Toros               Manhattan   
2  40.704053 -74.012071  10004  Toro Loco               Manhattan   
3  40.707778 -74.013507  10006  Tajin                   Manhattan   
4  40.705548 -74.012208  10004  El Toro                 Manhattan   

   SubBoroNumber                Neighborhood ZipCode  Name  
0  1              Battery Park City, Tribeca  10004   0.0   
1  1              Battery Park City, Tribeca  10004   1.0   
2  1              Battery Park City, Tribeca  10004   2.0   
3  1              Battery Park City, Tribeca  10006   3.0   
4  1              Battery Park City, Tribeca  10004   4.0

In [224]:
# Create a heat map with a marker for each venue, with the
# neighborhood boundaries overlayed on the map

# Make sure lat/lon are floats
dfAllVenues['lat'] = dfAllVenues['lat'].astype(float)
dfAllVenues['lon'] = dfAllVenues['lon'].astype(float)

# Make a list of lat/lon points of all the venues
heatMapData = [[row['lat'],row['lon']] for index, row in dfAllVenues.iterrows()]
HeatMap(heatMapData).add_to(map_manhattan)

   
# Add the centroid of each neighborhood to its geopandas DataFrame so we know
# where to put a text label identifying the neighborhood
nyBoundaries3["neighborhoodCentroid"] = nyBoundaries3.centroid
for index, row in nyBoundaries3.iterrows():
    textMarker = folium.Marker(location=[row.neighborhoodCentroid.y, row.neighborhoodCentroid.x], popup=row.Name)
    map_manhattan.add_child(textMarker)

map_manhattan

## Clustering

In [225]:
dfAllVenues.columns

Index(['category', 'id', 'address', 'city', 'lat', 'lon', 'zip', 'name',
       'Borough', 'SubBoroNumber', 'Neighborhood', 'ZipCode', 'Name'],
      dtype='object')

In [226]:
venues_onehot = pd.get_dummies(dfAllVenues[['category']], prefix="", prefix_sep="")
# add neighborhood column back to dataframe
venues_onehot['lat'] = dfAllVenues['lat'] 
venues_onehot['lon'] = dfAllVenues['lon'] 

venues_onehot.head()

Jazz Club  Mexican Restaurant        lat        lon
0  0          1                   40.704888 -74.012846
1  0          1                   40.702289 -74.013072
2  0          1                   40.704053 -74.012071
3  0          1                   40.707778 -74.013507
4  0          1                   40.705548 -74.012208

In [227]:
from sklearn.cluster import KMeans 

# set number of clusters
kclusters = 10

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(venues_onehot)

In [228]:
# add clustering labels to the dataframe, and add back the venue names
venues_onehot.insert(0, 'ClusterLabel', kmeans.labels_)
venues_onehot['name'] = dfAllVenues['name'] 
venues_onehot['category'] = dfAllVenues['category'] 
venues_onehot.head()


ClusterLabel  Jazz Club  Mexican Restaurant        lat        lon  \
0  3             0          1                   40.704888 -74.012846   
1  3             0          1                   40.702289 -74.013072   
2  3             0          1                   40.704053 -74.012071   
3  3             0          1                   40.707778 -74.013507   
4  3             0          1                   40.705548 -74.012208   

                     name            category  
0  Chipotle Mexican Grill  Mexican Restaurant  
1  Dos Toros               Mexican Restaurant  
2  Toro Loco               Mexican Restaurant  
3  Tajin                   Mexican Restaurant  
4  El Toro                 Mexican Restaurant

In [229]:
pd.value_counts(venues_onehot['ClusterLabel'])

3    419
8    208
2    199
4    108
0    105
6    94 
5    90 
1    58 
7    50 
9    26 
Name: ClusterLabel, dtype: int64

In [230]:
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
import folium

from folium.plugins import MarkerCluster

# create map
#map_clusters = folium.Map(location=manhattanCenter, zoom_start=11)
map_clusters = map_manhattan

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

#map_clusters

In [231]:
# Create a list of N MarkerCluster objects
# We'll treat this list like an array, using it to add
# venues to the appropriate marker cluster for the cluster map
numClusters = len(venues_onehot['ClusterLabel'].unique())
mcList = [MarkerCluster] * numClusters
nIndex = 0
for mc in mcList:
    mcList[nIndex] = MarkerCluster()
    nIndex = nIndex + 1


In [235]:
# add cluster markers to the map, with a cluster child for each top venue
# iterate over the rows in the DataFrame
for clusterRow in venues_onehot.itertuples():
    lat = clusterRow.lat
    lon = clusterRow.lon
    name = clusterRow.name
    category = clusterRow.category
    clusterNumber = clusterRow.ClusterLabel
    mc = mcList[clusterNumber]

    markerColor = dfMapMarkers.loc[category].color
    markerIconPrefix = dfMapMarkers.loc[category].icon_prefix
    markerIconName = dfMapMarkers.loc[category].icon_name
    thePopup = folium.Popup(name)
#    mc.add_child(folium.Marker(location=[lat,  lon], popup=thePopup, icon=folium.Icon(color='red', icon='info-sign')))
#    mc.add_child(folium.Marker(location=[lat,  lon], popup=thePopup, icon=folium.Icon(color='red', icon='glyphicon-music')))
    mc.add_child(folium.Marker(location=[lat,  lon], popup=thePopup, icon=folium.Icon(color=markerColor, prefix=markerIconPrefix, icon=markerIconName)))

for mc in mcList:
    map_clusters.add_child(mc)
    
map_clusters